In [1]:
import gc, argparse, sys, os, errno
%pylab inline
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
#sns.set()
#sns.set_style('whitegrid')
import h5py
from PIL import Image
import os
from tqdm.notebook import tqdm
import scipy
import sklearn
from scipy.stats import pearsonr
import warnings
warnings.filterwarnings('ignore')
sys.path.append('/scratch/xc1490/projects/tmp/python_packages')
sys.path.append('/scratch/xc1490/projects/tmp/python_packages/') #pip install --target=/home/xc1490/home/projects/tmp/python_packages package_name

Populating the interactive namespace from numpy and matplotlib


In [2]:
import warnings
warnings.filterwarnings('ignore')
import gc, argparse, sys, os, errno
%pylab inline
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt;
import seaborn as sns
#sns.set()
#sns.set_style('whitegrid')
import h5py
from PIL import Image
import os
from tqdm import tqdm_notebook as tqdm
import scipy
import sklearn
from scipy.stats import pearsonr
from scipy.io import loadmat
import IPython.display as ipd
import IPython
import librosa.display
import librosa
from pystoi import stoi

from mcd import dtw
import mcd.metrics as mt
def mel_cep_dtw_dist(target, converted):
    """
    Compute the distance between two unaligned speech waveforms
    :param target: reference speech numpy array
    :param converted: synthesized speech numpy array
    :return: mel cep distance in dB
    """
    total_cost = 0
    total_frames = 0
    for (tar, conv) in zip(target, converted):
        tar, conv = tar.astype('float64'), conv.astype('float64')
        cost, _ = dtw.dtw(tar, conv, mt.logSpecDbDist)
        frames = len(tar)
        total_cost += cost
        total_frames += frames

    return total_cost / total_frames
def play(audio,sr=16000):
    '''
    audio: tensor, eg: ex['audio']
    '''
    if len(audio.shape) >=2:
        audio = audio.ravel()
    display(ipd.Audio(audio,rate=sr))
def plot_stft(audio,ax=None,n_fft=256,hop_length=128,show=False,n_mels=128,y_axis='mel'):
    X = librosa.stft(audio,n_fft=n_fft,hop_length=hop_length)
    if y_axis=='mel':
        #x_stft_db = librosa.feature.melspectrogram(x, sr=16000,n_fft=n_fft,win_length=win_length,hop_length=hop_length)
        S = librosa.feature.melspectrogram(audio, sr=16000,n_mels=n_mels,fmax=8000,n_fft=n_fft,hop_length=hop_length)
        #print (S.shape)
        if show:
            librosa.display.specshow(librosa.power_to_db(S,
                                              ref=np.max),
                             y_axis='mel',cmap='gray_r',ax=ax, fmax=8000)
        else:
            spec_db = librosa.power_to_db(S,ref=np.max)
            #level = 80
            #spec_db[spec_db<=-level] = -100
            #spec_db[spec_db==-level] = -100
            return spec_db
    else:
        if show:
            specshow(librosa.amplitude_to_db(abs(X)),cmap=cm.Blues,#cm.gray_r,
                                      sr=16000,ax=ax)
        else:
            return librosa.amplitude_to_db(abs(X))
    
def MSE_pcc(A,B,ax=None):
    mse =np.mean(((A - B)**2/B.var()))
    pcc = pearsonr(A.ravel(),B.ravel())[0]
    return mse,pcc
def analyze(predict,GT_STFT_test_spkr,audio_pred,audio_gt,mode='test',ind=-1,plot=False,mcd=None):
    samples = predict.shape[0]
    pcc = np.zeros([samples])
    mse = np.zeros([samples])
    for i in range(samples):
        mse[i], pcc[i] = MSE_pcc(predict[i],GT_STFT_test_spkr[i])
        #mse[i], pcc[i] = MSE_pcc(predict[i] ,GT_STFT_test_spkr[i] )
    stois = []
    timedur = 0#0.06

    for i in range(samples):
        stois.append(stoi(np.concatenate((np.ones([int(interval*timedur)]),\
                audio_pred[i*interval:(i+1)*interval],np.ones([int(interval*timedur)]))), \
                          np.concatenate((np.ones([int(interval*timedur)]),\
                audio_gt[i*interval:(i+1)*interval],np.ones([int(interval*timedur)]))), 16000, extended=False))
    stois = np.array(stois)
    if plot:
        if mcd is not None:
            fig,ax=plt.subplots(1,4,figsize=(18,4))
            ax[3].hist(mcd,bins=50,color='m')
            ax[3].set_title(mode+' MCD: %g(%g)' %(np.round(mcd.mean(),3),np.round(mcd.std(),3)))
        else:
            fig,ax=plt.subplots(1,3,figsize=(20,4))
        #fig,ax=plt.subplots(1,3,figsize=(18,4))
        ax[0].hist(mse,bins=25,color='b')
        ax[0].set_title('ind '+str(ind)+' '+mode+' MSE: %g(%g)' %(np.round(mse.mean(),3),np.round(mse.std(),3)))
        ax[1].hist(pcc,bins=50,color='g')
        ax[1].set_title(mode+' PCC: %g(%g)' %(np.round(pcc.mean(),3),np.round(pcc.std(),3)))
        ax[2].hist(stois,bins=50,color='r')
        ax[2].set_title(mode+' STOI: %g(%g)' %(np.round(stois.mean(),3),np.round(stois.std(),3)))
    return mse,pcc,stois
def play(audio,sr=16000):
    '''
    audio: tensor, eg: ex['audio']
    '''
    if len(audio.shape) >=2:
        audio = audio.ravel()
    display(ipd.Audio(audio,rate=sr))
    
def amplitude(x,noise_db=-50,max_db=22.5,trim_noise=True):
   if trim_noise:
      x_db = (x+1)/2*(max_db-noise_db)+noise_db
      if type(x) is np.ndarray:
         return 10**(x_db/10)*(x_db>noise_db).astype(np.float32)
      else:
         return 10**(x_db/10)*(x_db>noise_db).float()
   else:
      return 10**(((x+1)/2*(max_db-noise_db)+noise_db)/10)
    
def log_spec_dB_dist(x, y):
    log_spec_dB_const = 10.0 / math.log(10.0) * math.sqrt(2.0)
    diff = x - y
    
    return log_spec_dB_const * math.sqrt(np.inner(diff, diff))
    
interval = 16383


def gradient_func(val):
    row, col = val.split('|')
    row, col = int(row), int(col)
    split1, split2 = df.iloc[row, col].split('/') #metric
    format_use = float(split2)*100
    color = 'black'#{'pass': 'green', 'fail': 'red', 'warn': 'orange'}.get(status, 'gray')
    if col!=4: 
        return '<a href="{sample_id}/result_final_{sample_id}.html" style="color: {color}"><span style="background: linear-gradient(90deg, rgba(61,164,166,1) {format_use}%, transparent 0%)">{split1:.3f}|{split2:.3f}</span></a>'.format(
            sample_id=int(df.columns[col][2:]),  color=color, split1=float(split1),split2=float(split2),format_use=format_use)
    else:
        return '<span style="background: linear-gradient(90deg, rgba(61,164,166,1) {format_use}%, transparent 0%)">{split1:.3f}|{split2:.3f}</span>'.format(
            sample_id=df.columns[col], area_id =df.index[row], color=color, split1=float(split1),split2=float(split2),format_use=format_use)

#df_index.style.format(style_func)
def display_dataframe(df, filename=None, encoding='utf-8', format='csv', type='button',gradientfunc=False, **kwargs):
    #display(df)
    #if isinstance(df, pd.DataFrame):
    #    display(df.style.set_caption(filename))
    #else:
    if gradientfunc == False:
        display(df.style.set_caption(filename))    
    else:
        display(df.style.format(gradient_func).set_caption(filename)) 
    if filename is None:
        filename = "dataframe"
    if format == 'csv':
        data = df.to_csv(**kwargs)
        mime_type = 'text/csv'
        filename = filename + '.csv'
    elif format == 'tsv':
        data = df.to_csv(**kwargs)
        mime_type = 'text/plain'
        filename = filename + '.txt'
    else:
        raise ValueError('unknown file format: {}'.format(format))
    data = 'data:{mime_type};base64,'.format(mime_type=mime_type) + str(b64encode(bytes(data, encoding=encoding)), encoding=encoding)
    if type == 'hyperlink':
        display(HTML('<a href=" " download={filename} target="_blank">{filename}</a >'.format(
            mime_type=mime_type, filename=filename, data=data)))
    elif type == 'button':
        button_id = 'button_{}'.format(np.random.randint(1000000000))
        display(HTML(r'<input type="button" id="{0}" value="Download">'.format(button_id)))
        display(HTML('''<script>
    document.getElementById("{button_id}").addEventListener("click", function(event){{
        var filename = "{filename}";
        var data = "{data}";
        const element = document.createElement('a');
        element.setAttribute('href', data);
        element.setAttribute('download', filename);
        element.style.display = 'none';
        document.body.appendChild(element);
        element.click();
        document.body.removeChild(element);
    }});
</script>'''.format(button_id=button_id, filename=filename, data=data)))
        
from matplotlib.backends.backend_pdf import PdfPages, PdfFile
from IPython.display import HTML, display, FileLink
from base64 import b64encode, b64decode
from io import StringIO, BytesIO
from contextlib import contextmanager

sys.path.append('/scratch/xc1490/projects/tmp/python_packages')
sys.path.append('/scratch/xc1490/projects/ecog/ALAE_1023/')
sys.path.append('/scratch/xc1490/projects/tmp/python_packages/') #pip install --target=/home/xc1490/home/projects/tmp/python_packages package_name
from pesq import pesq
#PESQ (Perceptual Evaluation of Speech Quality) Wrapper for Python Users
#https://github.com/ludlows/PESQ
#!pip install --target=/home/xc1490/home/projects/tmp/python_packages pesq
from metrics.pystoi_plus import stoi_plus #stoi+
#pip install --target=/home/xc1490/home/projects/tmp/python_packages https://github.com/schmiph2/pysepm/archive/master.zip
#https://github.com/schmiph2/pysepm
import pysepm
def MTF(wave, n_fft = 160):
    S = librosa.stft(wave,n_fft=n_fft)#,hop_length=hop_length) #16000 * 0.01
    F= np.fft.fftshift(np.log(np.abs(np.fft.fft2(np.log(np.abs(S))))))
    return F[ :F.shape[0]//2, F.shape[1]//2 - 10: F.shape[1]//2 + 10 ]

def MTF_corr(orig_wave, pred_wave):
    F_tmp_orig = MTF(orig_wave)
    F_tmp_pred = MTF(pred_wave)
    F_tmp_pred_1 = F_tmp_pred[-5:,F_tmp_pred.shape[1]//2 -  4: F_tmp_pred.shape[1]//2 +  4 ]
    #F_tmp_pred_2 = F_tmp_pred[-5:]
    F_tmp_orig_1 = F_tmp_orig[-5:,F_tmp_orig.shape[1]//2 -  4: F_tmp_orig.shape[1]//2 +  4 ]
    #F_tmp_orig_2 = F_tmp_orig[-5:]
    return pearsonr(F_tmp_orig.ravel(),F_tmp_pred.ravel())[0], pearsonr(F_tmp_pred_1.ravel(),F_tmp_orig_1.ravel())[0]


def get_result_dict(model_dir, sampleind,epooch=None):
    if epooch is None:
    #print ([int(i.split('.')[1].split('_')[-1]) for i in os.listdir(model_dir) if i.endswith('npy')])
        try:
            epooch = int(np.max([int(i.split('.')[1].split('_')[-1]) for i in os.listdir(model_dir) if i.endswith('npy')]))
        except:
            epooch = int(np.max([int(i.split('.')[-3].split('_')[-2]) for i in os.listdir(model_dir) if i.endswith('_.pngdenoise.wav')])) 
        
    result_dict = np.load(model_dir+'sample_{}_{}.png_sample_npy_{}.npy'.format(epooch,sampleind,epooch),allow_pickle=1).item()
    #print (result_dict.keys())
    wave_key_list = ['wave_org_denoise','wave_rec','wave_rec_denoise' ]
    for key in result_dict.keys():
        if key!='components' and key!='components_ecog' and key!='lable':
            #print (key)
            #print (key,result_dict[key].shape)
            if key =='org_denoise':
                result_dict[key] = amplitude(result_dict[key])
            if key =='rec_denoise' or key =='rec_ecog' or key =='rec_ecog_denoise' or key =='org' or key =='rec':
                result_dict[key] = (result_dict[key]-0.5)*2
            if key in wave_key_list:
                #print (key)
                factor = np.sqrt(sum(result_dict['wave_org']**2)/sum(result_dict[key]**2))
                result_dict[key] = result_dict[key]*factor
    #for key in ['org','rec', 'rec_denoise']:
    #    result_dict[key] = np.swapaxes(result_dict[key].reshape(256,50,-1),1,0)
    return result_dict
sample_num = 50
fs = 16000
def get_metric_from_result_dict(result_dict,patient_num =50):

    #a2a
    spec_gt = result_dict['org']
    spec_pred = result_dict['rec']
    #spec_gt_mel =  np.array([librosa.feature.melspectrogram(S=spec_gt [i] , sr=16000,n_fft=511,hop_length=129,n_mels=256,fmax=8000) \
    #                                    for i in range(50)]) 
    #spec_pred_mel =  np.array([librosa.feature.melspectrogram(S=spec_pred[i] , sr=16000,n_fft=511,hop_length=129,n_mels=256,fmax=8000) \
    #                                      for i in range(50)])
    #mcds = []
    #frames = 128
    #for i in range(50):
     #   spec_gt_tmp = spec_gt_mel[i]
     #   spec_pred_tmp = spec_pred_mel[i]
     #   total_cost =0
     #   mcds.append(np.mean(librosa.sequence.dtw(spec_gt_tmp[1: ], spec_pred_tmp[1: ], metric=log_spec_dB_dist)[0])/frames)

    wave_gt = result_dict['wave_org'][:,0,:].ravel()
    wave_pred =result_dict['wave_rec'][:819582//interval*interval].ravel()

    spec_pred_mel = np.zeros([patient_num,32,127])
    spec_gt_mel = np.zeros([patient_num,32,127])

    for i in  range(patient_num):
        spec_pred_mel[i] = plot_stft(wave_pred[i*interval:(i+1)*interval],n_fft=511,hop_length=129,ax=None ,y_axis='mel',n_mels=32)
        spec_gt_mel[i] = plot_stft(wave_gt[i*interval:(i+1)*interval],n_fft=511,hop_length=129,ax=None,y_axis='mel',n_mels=32 )
    spec_concat_a2a = np.concatenate(( np.flip(spec_gt_mel,axis=1), np.flip(spec_pred_mel,axis=1)),axis=1)
    
    #mcds = []
    #for i in  range(50) :
    #    mcds.append(mel_cep_dtw_dist(spec_pred_mel[i].T[:,1:]/10,spec_gt_mel[i].T[:,1:]/10))
    #mcds = np.array(mcds)
    #mcd_a2a = mcds
    
    mse_test_a2a,pcc_test_a2a,stois_test_a2a = analyze(spec_pred_mel,spec_gt_mel,wave_pred,wave_gt,plot=False,mcd=None)

    

    #mfcc a2a
    wave_gt = result_dict['wave_org'][:,0,:].ravel()
    wave_pred =result_dict['wave_rec'][:819582//interval*interval].ravel()

    spec_pred = np.zeros([patient_num,32,32])
    spec_gt = np.zeros([patient_num,32,32])

    mfcc_a2a = np.zeros([patient_num])
    for i in  range(patient_num):
        spec_pred[i] = librosa.feature.mfcc(y=wave_pred[i*interval:(i+1)*interval], sr=16000,n_mfcc=32)
        spec_gt[i] = librosa.feature.mfcc(y=wave_gt[i*interval:(i+1)*interval], sr=16000,n_mfcc=32)
        mfcc_a2a[i] = pearsonr(spec_pred[i].ravel(),spec_gt[i].ravel())[0]
    MTF_cc_a2a = np.zeros([sample_num])
    MTF_cc_a2a1 = np.zeros([sample_num])
    for i in  range(sample_num):
        try:
            MTF_cc_a2a[i],MTF_cc_a2a1[i] = MTF_corr(wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval])
        except:
            MTF_cc_a2a[i],MTF_cc_a2a1[i] = np.nan, np.nan
    stoi_extended_a2a = np.array([stoi(wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval], fs, extended=True) for i in   range(sample_num) ])
    stoi_plus_a2a = np.array([stoi_plus(wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval], fs, extended=False) for i in   range(sample_num) ])
    pesq_wb_a2a = np.zeros([sample_num])
    pesq_wb_a2a[:] = numpy.nan
    for i in range(sample_num) :
        try:
            pesq_wb_a2a[i] =  pesq(fs, wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval], 'wb') 
        except:
            pass
    pesq_nb_a2a = np.zeros([sample_num])
    pesq_nb_a2a[:] = numpy.nan
    for i in range(sample_num) :
        try:
            pesq_nb_a2a[i] =  pesq(fs, wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval], 'nb') 
        except:
            pass
    csii_a2a = np.array([pysepm.csii(wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval], fs ) for i in  range(sample_num) ])
    ncm_a2a =  np.zeros([sample_num,32,127])#np.array([pysepm.ncm(wave_gt[i*interval:(i+1)*interval], wave_pred[i*interval:(i+1)*interval], fs ) for i in  range(sample_num) ])
    
    return  mse_test_a2a, pcc_test_a2a, stois_test_a2a, None, mfcc_a2a, MTF_cc_a2a,   \
            MTF_cc_a2a1, stoi_extended_a2a, stoi_plus_a2a, pesq_wb_a2a, pesq_nb_a2a, csii_a2a, ncm_a2a

def split_table(all_table,samples=[]):
    ref_table = pd.DataFrame(np.zeros([all_table.shape[0], all_table.shape[1]]).astype('str'))
    for i in range(all_table.shape[0]):
        for j in range(all_table.shape[1]):
            ref_table.iloc[i,j] = all_table.iloc[i,j].split('/')[0]
    ref_table.index = ['SPEC','STOI','MFCC','MCD']
    ref_table.columns = samples
    decode_table = pd.DataFrame(np.zeros([all_table.shape[0], all_table.shape[1]]).astype('str'))
    for i in range(all_table.shape[0]):
        for j in range(all_table.shape[1]):
            decode_table.iloc[i,j] = all_table.iloc[i,j].split('/')[1]
    decode_table.index = ['SPEC','STOI','MFCC','MCD']
    decode_table.columns = samples
    return ref_table.astype('float'), decode_table.astype('float')

def get_decoded_table(exp_name):
    return split_table(pd.read_table('../{}/formant_metric_summary_multicompare.csv'.format(exp_name),\
                                                    delimiter=',',index_col=0).iloc[:,:-1])
def generate_plot_table(df_table,exp_name='pre_arti'):
    df = pd.DataFrame( np.concatenate((df_table.values.reshape(-1,1),np.array(np.repeat(df_table.index,3)).reshape(-1,1),\
                np.concatenate([df_table.columns for i in range(4)]).reshape(-1,1) ,\
                 np.repeat(exp_name,df_table.shape[0]*df_table.shape[1]).reshape(-1,1)),axis=1) )
    df.columns = ['value','metric','sample','exp']
    return df
def extract_table(datapath,metric_csv,metric_name,exp_name):
    dftmp = pd.read_table(datapath+'formant_metric_summary_{}_multicompare.csv'.format(metric_csv),\
                                                        delimiter=',',index_col=0)
    ref_table, decode_table = dftmp[dftmp.task=='Reference'], dftmp[dftmp.task=='Decoded']
    ref_table['exp'] = 'Speech-to-Speech'
    ref_table['metric'] = metric_name
    decode_table['exp'] = exp_name
    decode_table['metric'] = metric_name
    return ref_table, decode_table
def concat_table(datapath = '../', exp_name = 'all',ref=False):
    ref_table_spec, decode_table_spec = extract_table(datapath=datapath,metric_csv='spec',metric_name='SPEC correlation',exp_name=exp_name)
    ref_table_stoi, decode_table_stoi = extract_table(datapath=datapath,metric_csv='stoi',metric_name='STOI',exp_name=exp_name)
    #ref_table_mfcc, decode_table_mfcc = extract_table(datapath=datapath,metric_csv='mfcc',metric_name='MFCC correlation',exp_name=exp_name)
    #ref_table_mcd, decode_table_mcd = extract_table(datapath=datapath,metric_csv='mcd',metric_name='MCD',exp_name=exp_name)
    if ref:
        return pd.concat((ref_table_spec,decode_table_spec,ref_table_stoi, decode_table_stoi))#,ref_table_mfcc, decode_table_mfcc,\
              #ref_table_mcd, decode_table_mcd))
    else:
        return pd.concat(( decode_table_spec,  decode_table_stoi))#,  decode_table_mfcc,\
                #decode_table_mcd))
# for fig1-3
flatui = ['#FEAC49', '#76C577', '#6AAED1', '#E68163', '#969696']
sns.color_palette(flatui)
sns.set_palette(sns.color_palette(flatui))


import json
with open('/scratch/xc1490/home/projects/ecog/ALAE_1023/AllSubjectInfo.json','r') as rfile:
    allsubj_param = json.load(rfile)

def display_and_plot(pcc_onset, result_dict,sample_ind):
    subj_param = allsubj_param['Subj'][ str(sample_ind)]
    Gender = subj_param['Gender']
    print ('*'*20,sample_ind, Gender,'*'*20)
    wave_gt = result_dict['wave_org'].ravel()
    wave_pred_a2a = result_dict['wave_rec'].ravel()
    #wave_pred = result_dict['wave_rec_ecog'].ravel()
    wave_merge = np.concatenate(([np.concatenate((wave_gt[i*interval:(i+1)*interval],wave_pred_a2a[i*interval:(i+1)*interval]))\
                     for i in range(50)]))

    print ('original')
    display(ipd.Audio(wave_gt.reshape(50,-1)[np.argsort(-pcc_onset)].ravel(),rate=16000))
    print ('a2a pred')
    display(ipd.Audio(wave_pred_a2a.reshape(50,-1)[np.argsort(-pcc_onset)].ravel(),rate=16000))
    #print ('e2a pred')
    #display(ipd.Audio(wave_pred.reshape(50,-1)[np.argsort(-pcc_onset)].ravel(),rate=16000))
    print ('merge of orig and a2a pred')
    display(ipd.Audio(wave_merge.reshape(50,-1)[np.argsort(-pcc_onset)].ravel(),rate=16000))
    if Gender == 'Female':
        N_FFT = 511 
        plot_factor = 1
    else:
        N_FFT =1023
    plot_factor = 1.6
    spec_dim = 127
    spec_pred = np.zeros([50,(N_FFT+1)//2,spec_dim])
    spec_gt = np.zeros([50,(N_FFT+1)//2,spec_dim])
    try:
        select_word = np.loadtxt('/scratch/xc1490/home/projects/ecog/ALAE_1023/data/wordlist_{}.txt'.format(sample_ind),dtype='str')
    except:
        pass
    #print (select_word)
    
    
    
    for i in range(50):
        spec_pred[i] = plot_stft(wave_pred_a2a[i*interval:(i+1)*interval],n_fft=N_FFT,hop_length=129,ax=None ,y_axis='linear',n_mels=32)
        spec_gt[i] = plot_stft(wave_gt[i*interval:(i+1)*interval],n_fft=N_FFT,hop_length=129,ax=None,y_axis='linear',n_mels=32 )
        #spec_pred[i] = plot_stft(wave_pred[i*interval:(i+1)*interval],n_fft=511,hop_length=129,ax=None ,y_axis='linear',n_mels=256)
        #spec_gt[i] = plot_stft(wave_gt[i*interval:(i+1)*interval],n_fft=511,hop_length=129,ax=None,y_axis='linear',n_mels=256 )
    spec_concat = np.concatenate(( np.flip(spec_gt,axis=1), np.flip(spec_pred,axis=1)),axis=1)
    spec_concat = np.concatenate(( np.flip(spec_gt,axis=1), np.flip(spec_pred,axis=1)),axis=1)

    row_nums = 5
    col_nums = 10
    fig,ax=plt.subplots(row_nums,col_nums,figsize=(col_nums*1.4,row_nums*4*plot_factor))
    cmap = cm.gray_r
    for i in range(row_nums):
        for j in range(col_nums):
            ax[i,j].imshow(spec_concat[np.argsort(-pcc_onset)[i*col_nums+j]] ,cmap=cmap)
            try:
                ax[i,j].set_title(select_word[np.argsort(-pcc_onset)[i*col_nums+j]]+' {0:.3g}'.format(pcc_onset[np.argsort(-pcc_onset)[i*col_nums+j]]))
                #ax[i,j].set_title(select_word[np.argsort(-pcc_test)[i*col_nums+j]]+' {0:.3g}'.format(-np.sort(-pcc_test)[i*col_nums+j]))
            except:
                pass

    plt.tight_layout()
    plt.show()
exclude_pcc = {'NY746':np.array([1,2,]),'NY746':np.array([2,]),'NY857':np.array([0,1,2,3,4,5,7,11])}


def extract_table2(datapath,metric_csv,metric_name,exp_name1,exp_name2,suffix=''):
    dftmp = pd.read_table(datapath+'formant_metric_summary_{}_multicompare_{}.csv'.format(metric_csv,suffix),\
                                                        delimiter=',',index_col=0)
    ref_table, decode_table = dftmp[dftmp.task=='Reference'], dftmp[dftmp.task=='Decoded']
    ref_table['exp'] = exp_name1
    ref_table['metric'] = metric_name
    decode_table['exp'] = exp_name2
    decode_table['metric'] = metric_name
    return ref_table, decode_table
def concat_table2(datapath = '../', exp_name1 = 'all',exp_name2 = 'all',ref=False,suffix=''):
    ref_table_spec, decode_table_spec = extract_table2(datapath=datapath,metric_csv='spec',metric_name='SPEC correlation',exp_name1=exp_name1,exp_name2=exp_name2,suffix=suffix)
    ref_table_stoi, decode_table_stoi = extract_table2(datapath=datapath,metric_csv='stoi',metric_name='STOI',exp_name1=exp_name1,exp_name2=exp_name2,suffix=suffix)
    #ref_table_mfcc, decode_table_mfcc = extract_table(datapath=datapath,metric_csv='mfcc',metric_name='MFCC correlation',exp_name=exp_name)
    #ref_table_mcd, decode_table_mcd = extract_table(datapath=datapath,metric_csv='mcd',metric_name='MCD',exp_name=exp_name)
    if ref:
        return pd.concat((ref_table_spec,decode_table_spec,ref_table_stoi, decode_table_stoi))#,ref_table_mfcc, decode_table_mfcc,\
              #ref_table_mcd, decode_table_mcd))
    else:
        return pd.concat(( decode_table_spec,  decode_table_stoi))#,  decode_table_mfcc,\


Populating the interactive namespace from numpy and matplotlib


In [3]:
cd /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/

/scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding


In [4]:
ls /scratch/xc1490/ECoG_Shared_Data/demo/output_new/a2a_1005/a2a_10050800_a2a_corpus_sub_NY869_nsample_80_nfft_512_noisedb_-50_density_LD_formantsup_1_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0

model_epoch95.pth*        sample_96_NY869.png_sample_npy_96.npy*
result_96_NY869.png*      sample_96_NY869.pngdenoise.wav*
result_train_96_.png*     sample_train_96_.png*
sample_96_NY869.png*      sample_train_96_.png.wav*
sample_96_NY869.png.wav*  sample_train_96_.pngdenoise.wav*


In [7]:
root_dir = '/scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/869model/'
quantifiles = np.sort(os.listdir(root_dir))
quantifiles = [root_dir+i for i in quantifiles]
root_dir = '/scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/multisubjectmodel/'
quantifiles2 = np.sort(os.listdir(root_dir))
quantifiles2 = [root_dir+i for i in quantifiles2]
quantifiles = np.concatenate((quantifiles, quantifiles2)).ravel()

In [7]:
sample = 'NY869'
root_dir = '/scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/'
quantifiles = ['{}_kmeans_model_Cluster{}_Window{}_6formants.pkl'.format(sample,cluster,window) 
    for cluster in [100,200,500,1000] for window in [1,2,3]]
quantifiles = [root_dir+i for i in quantifiles]
len(quantifiles)

12

In [ ]:
if allsubj_param['Subj'][subject]['Gender'] =='Female':
                        n_ffts = [256]
                    else:
                        n_ffts = [512]
                    for n_fft in n_ffts:

                        #if n_fft == 256:
                        #if allsubj_param['Subj'][subject]['Gender'] =='Male':
                                load_sub_dir = get_model_path(subject)#'output/a2a_05140800_a2a_corpus_sub_{}_nsample_80_nfft_{}_noisedb_-50_density_LD_formantsup_1_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0'.format( subject,n_fft )
                        #if os.path.exists( load_sub_dir):
                            #if len(os.listdir(load_sub_dir)) >= 10:
                                for n_filter_samples in [ 80 ]: #150????
                                    for dynamicfiltershape in [0 ]:#1???
                                        if subject =='NY829':
                                            n_filter_samples = 20
                                        ignore_loading = 0
                                        finetune = 1
                                        density = allsubj_param['Subj'][subject]['Density']

In [23]:
model_dirs = ['output_new/a2a_0814/quantization_INFER_a2a_08140800_a2a_corpus_sub_{}_nsample_{}_use_denoise_0_stoi_0_nfft_{}_noisedb_-50_density_{}_formantsup_0_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0_quantind_{}/'.format(
                sample, 80 if sample !='NY829' else 20, \
                256 if allsubj_param['Subj'][sample]['Gender'] =='Female' else 512,\
                allsubj_param['Subj'][sample]['Density'], quantind)
                for sample in ['NY869'] for quantind in range(len(quantifiles))  ]

In [24]:
for quantind in range(len(quantifiles)):
    #model_dir = 'output_new/a2a_0813/quantization_INFER_a2a_08130800_a2a_corpus_sub_NY869_nsample_80_use_denoise_0_stoi_0_nfft_512_noisedb_-50_density_LD_formantsup_0_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0_quantind_{}/'.format(quantind)
    print (quantind, quantifiles[quantind],len(os.listdir(model_dirs[quantind])))

0 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster100_Window1_6formants.pkl 6
1 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster100_Window2_6formants.pkl 6
2 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster100_Window3_6formants.pkl 6
3 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster200_Window1_6formants.pkl 6
4 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster200_Window2_6formants.pkl 6
5 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster200_Window3_6formants.pkl 6
6 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster500_Window1_6formants.pkl 6
7 /scratch/xc1490/projects/ecog/ALAE_1023/neural_speech

In [33]:
mse_test_a2a_dict, pcc_test_a2a_dict, stois_test_a2a_dict, mcd_a2a_dict, mfcc_a2a_dict, MTF_cc_a2a_dict,  \
MTF_cc_a2a_dict1, MTF_cc_e2a_dict1, stoi_extended_a2a_dict, stoi_plus_a2a_dict, pesq_wb_a2a_dict, pesq_nb_a2a_dict, csii_a2a_dict, ncm_a2a_dict = {},{},{},{},{},{},{},{},{},{},{},{},{},{}
count = 0

sample = 'NY869'
for quantind in tqdm(range(len(quantifiles))):
    model_dir = model_dirs[quantind] #'output_new/a2a_0813/quantization_INFER_a2a_08130800_a2a_corpus_sub_NY869_nsample_80_use_denoise_0_stoi_0_nfft_512_noisedb_-50_density_LD_formantsup_0_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0_quantind_{}/'.format(quantind)
    if os.path.exists(model_dir+'sample_1_{}.png_sample_npy_1.npy'.format(sample)):
        result_dict = np.load(model_dir+'sample_1_{}.png_sample_npy_1.npy'.format(sample),allow_pickle=True).item()#.keys()
        sample_ind = quantind
        mse_test_a2a_dict[sample_ind], pcc_test_a2a_dict[sample_ind],\
        stois_test_a2a_dict[sample_ind], mcd_a2a_dict[sample_ind], mfcc_a2a_dict[sample_ind],MTF_cc_a2a_dict[sample_ind],  MTF_cc_a2a_dict1[sample_ind],\
        stoi_extended_a2a_dict[sample_ind], stoi_plus_a2a_dict[sample_ind], pesq_wb_a2a_dict[sample_ind], pesq_nb_a2a_dict[sample_ind],\
        csii_a2a_dict[sample_ind], ncm_a2a_dict[sample_ind] \
                            = get_metric_from_result_dict(result_dict)
    else:
        print ('error',model_dir+'sample_1_{}.png_sample_npy_1.npy'.format(sample_ind))

  0%|          | 0/12 [00:00<?, ?it/s]

In [34]:
for quantind in range(len(quantifiles)):
    model_dir = model_dir = model_dirs[quantind]#'output_new/a2a_0813/quantization_INFER_a2a_08130800_a2a_corpus_sub_NY869_nsample_80_use_denoise_0_stoi_0_nfft_512_noisedb_-50_density_LD_formantsup_0_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0_quantind_{}/'.format(quantind)
    #print (quantind, model_dir)

In [35]:
[(quantifiles[quantind].split('/')[-1],'{:.3f}'.format(stois_test_a2a_dict[quantind].mean())) for quantind in range(len(quantifiles))]

[('NY869_kmeans_model_Cluster100_Window1_6formants.pkl', '0.671'),
 ('NY869_kmeans_model_Cluster100_Window2_6formants.pkl', '0.645'),
 ('NY869_kmeans_model_Cluster100_Window3_6formants.pkl', '0.619'),
 ('NY869_kmeans_model_Cluster200_Window1_6formants.pkl', '0.659'),
 ('NY869_kmeans_model_Cluster200_Window2_6formants.pkl', '0.640'),
 ('NY869_kmeans_model_Cluster200_Window3_6formants.pkl', '0.636'),
 ('NY869_kmeans_model_Cluster500_Window1_6formants.pkl', '0.671'),
 ('NY869_kmeans_model_Cluster500_Window2_6formants.pkl', '0.656'),
 ('NY869_kmeans_model_Cluster500_Window3_6formants.pkl', '0.631'),
 ('NY869_kmeans_model_Cluster1000_Window1_6formants.pkl', '0.687'),
 ('NY869_kmeans_model_Cluster1000_Window2_6formants.pkl', '0.672'),
 ('NY869_kmeans_model_Cluster1000_Window3_6formants.pkl', '0.637')]

In [ ]:
sample  = 'NY869'
for quantind in range(len(quantifiles)):
    model_dir = model_dirs[quantind] #'output_new/a2a_0813/quantization_INFER_a2a_08130800_a2a_corpus_sub_NY869_nsample_80_use_denoise_0_stoi_0_nfft_512_noisedb_-50_density_LD_formantsup_0_wavebased_1_bgnoisefromdata_1_load_0_ft_1_learnfilter_1_reverse_1_dynamic_0_quantind_{}/'.format(quantind)
    if os.path.exists(model_dir+'sample_1_{}.png_sample_npy_1.npy'.format(sample)):
        result_dict = np.load(model_dir+'sample_1_{}.png_sample_npy_1.npy'.format(sample),allow_pickle=True).item()#.keys()
        print ('*'*60)
        print ('stoi',stois_test_a2a_dict[quantind].mean())
        print (quantifiles[quantind])
        display_and_plot(np.ones([50]), result_dict,sample)

************************************************************
stoi 0.6705000387034196
/scratch/xc1490/projects/ecog/ALAE_1023/neural_speech_decoding/data/models/all/NY869_kmeans_model_Cluster100_Window1_6formants.pkl
******************** NY869 Male ********************
original


a2a pred


merge of orig and a2a pred
